# Imports

In [2]:
import json
#import nltk
import re
import pandas as pd
import numpy as np
from sklearn.cluster import KMeans
from sklearn.metrics import normalized_mutual_info_score
from sklearn.metrics import adjusted_rand_score
from scipy.optimize import linear_sum_assignment
#from nltk.corpus import stopwords
#from nltk.stem import WordNetLemmatizer
from sentence_transformers import SentenceTransformer, util
from dotenv import load_dotenv
import os
#from together import Together
from mistralai import Mistral
from sklearn.metrics.pairwise import cosine_similarity
load_dotenv()  
#from sklearn.feature_extraction.text import TfidfVectorizer
#from gensim.models import Word2Vec

c:\projetsAlternance\projetMasterGit\Clustering_and_LLMs\.venv\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


True

### LLama Model

In [6]:
together_api_key = os.getenv("TOGETHER_API_KEY")
#llama_client = Together(api_key=together_api_key)

### Mistral Model 

In [7]:
api_key = os.getenv("MISTRAL_API_KEY")
mistral = "mistral-large-latest"
mistral_client = Mistral(api_key=api_key)

#### Embeddings Models Import 

In [3]:
inst_emb_model = SentenceTransformer("hkunlp/instructor-xl") 
minilm_emb_model = SentenceTransformer("all-MiniLM-L6-v2") 

#### Download and Initialize NLP Tools


In [3]:
nltk.download('stopwords')
nltk.download('wordnet')
stop_words = set(stopwords.words('english'))
lemmatizer = WordNetLemmatizer()

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\melis\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\melis\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


#### Import Raw Data 

In [ ]:
data_path = "C:/ProjetMaster/text_clustering/dataset/clinc/data/data_full.json"

with open(data_path, 'r') as f:
    data = json.load(f)

filtered_data = []

for source in ['val', 'train', 'test']:
    for item in data.get(source, []):
        # Ajouter la phrase et le champ source
        filtered_data.append({
            "phrase": item[0],
            "intent": item[1],
            "source": source
        })

In [21]:
for d in filtered_data[0:5]:
    print(d)

{'phrase': 'in spanish, meet me tomorrow is said how', 'intent': 'translate', 'source': 'val'}
{'phrase': 'in french, how do i say, see you later', 'intent': 'translate', 'source': 'val'}
{'phrase': 'how do you say hello in japanese', 'intent': 'translate', 'source': 'val'}
{'phrase': 'how do i ask about the weather in chinese', 'intent': 'translate', 'source': 'val'}
{'phrase': 'how can i say "cancel my order" in french', 'intent': 'translate', 'source': 'val'}


In [22]:
# Compter les éléments dans chaque source
count_val = len([data for data in filtered_data if data["source"] == "val"])
count_train = len([data for data in filtered_data if data["source"] == "train"])
count_test = len([data for data in filtered_data if data["source"] == "test"])

# Afficher les résultats
print(f"Nombre de données 'val' : {count_val}")
print(f"Nombre de données 'train' : {count_train}")
print(f"Nombre de données 'test' : {count_test}")

Nombre de données 'val' : 3000
Nombre de données 'train' : 15000
Nombre de données 'test' : 4500


In [23]:
intents = [data['intent'] for data in filtered_data]

for intent in set(intents): 
    count = intents.count(intent)
    print(f"Nombre de données {intent}: {count}")

Nombre de données cook_time: 150
Nombre de données what_is_your_name: 150
Nombre de données gas: 150
Nombre de données schedule_maintenance: 150
Nombre de données directions: 150
Nombre de données current_location: 150
Nombre de données plug_type: 150
Nombre de données rewards_balance: 150
Nombre de données calculator: 150
Nombre de données pto_used: 150
Nombre de données todo_list: 150
Nombre de données international_fees: 150
Nombre de données reminder_update: 150
Nombre de données are_you_a_bot: 150
Nombre de données last_maintenance: 150
Nombre de données pin_change: 150
Nombre de données fun_fact: 150
Nombre de données pto_request_status: 150
Nombre de données smart_home: 150
Nombre de données reset_settings: 150
Nombre de données how_busy: 150
Nombre de données play_music: 150
Nombre de données definition: 150
Nombre de données flight_status: 150
Nombre de données change_language: 150
Nombre de données restaurant_reservation: 150
Nombre de données who_made_you: 150
Nombre de donn

In [24]:
texts = [item['phrase'] for item in filtered_data]
true_labels = [data['intent'] for data in filtered_data]  

#### Text pre-processing

In [25]:
def preprocess_text(text):
    text = text.lower() 
    text = re.sub(r'\W+', ' ', text)  
    words = text.split()
    words = [lemmatizer.lemmatize(word) for word in words if word not in stop_words]  
    return ' '.join(words)

In [10]:
texts = [preprocess_text(text).split() for text in texts]

# Evaluation Functions

In [4]:
def compute_nmi(true_labels_texts, predicted_labels):
    nmi_score = normalized_mutual_info_score(true_labels_texts, predicted_labels)
    return nmi_score

In [5]:
def compute_hungarian_accuracy(true_labels, predicted_labels):
    true_labels = pd.factorize(true_labels)[0]  
    predicted_labels = pd.factorize(predicted_labels)[0]
    
    max_label = max(max(true_labels), max(predicted_labels)) + 1
    cost_matrix = np.zeros((max_label, max_label))

    for i in range(len(true_labels)):
        cost_matrix[true_labels[i], predicted_labels[i]] += 1

    row_ind, col_ind = linear_sum_assignment(cost_matrix, maximize=True)
    accuracy = cost_matrix[row_ind, col_ind].sum() / len(true_labels)
    return accuracy

In [6]:
def compute_ari(true_labels_texts, predicted_labels):
    ari = adjusted_rand_score(true_labels_texts, predicted_labels)
    return ari

# Vectorization

### TF-IDF Vectorization 

In [ ]:
vectorizer = TfidfVectorizer(stop_words='english')
X = vectorizer.fit_transform(texts)

In [ ]:
print(X.shape)

(22500, 5956)


### Word2Vec Vectorization  

In [ ]:
model = Word2Vec(sentences=texts, vector_size=300, window=5, min_count=3, sg=1)

In [31]:
def document_embedding(document, model):
    word_embeddings = []
    for word in document:
        if word in model.wv:
            word_embeddings.append(model.wv[word])
    if len(word_embeddings) == 0:
        return np.zeros(model.vector_size)
    else:
        return np.mean(word_embeddings, axis=0)

In [32]:
# Compute the document embeddings
X = np.array([document_embedding(doc, model) for doc in texts])

In [33]:
print(X.shape)


(22500, 300)


### Bert Model Vectorization

In [13]:
X = minilm_emb_model.encode(texts)

### Instructor Vectorization

In [ ]:
prompt = "Represent the sentence for intent clustering: "

texts_with_prompt = [f"{prompt} {text}" for text in texts]

X = inst_emb_model.encode(
      texts_with_prompt,
      batch_size=16,
      convert_to_numpy=True,
      show_progress_bar=True
)

# Train Test Data 

In [15]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X, true_labels, stratify=true_labels, test_size=0.2, random_state=42)

In [ ]:
kmeans = KMeans(n_clusters=len(set(true_labels)), random_state=42)
kmeans.fit(X_train)

y_train_pred = kmeans.predict(X_train)
y_test_pred = kmeans.predict(X_test)

In [ ]:
# Sur train
ari_train = adjusted_rand_score(y_train, y_train_pred)
nmi_train = normalized_mutual_info_score(y_train, y_train_pred)

# Sur test
ari_test = adjusted_rand_score(y_test, y_test_pred)
nmi_test = normalized_mutual_info_score(y_test, y_test_pred)

print(f"Train ARI : {ari_train:.2f}, NMI : {nmi_train:.2f}")
print(f"Test  ARI : {ari_test:.2f}, NMI : {nmi_test:.2f}")

Train ARI : 0.69, NMI : 0.89
Test  ARI : 0.68, NMI : 0.90


# LLMs Approaches

## Before Clustering

### Sentence Reformulation

In [ ]:
def rewrite_with_intent(text):
    prompt = (
        "Reformulate the following sentence to make its intent more explicit while maintaining a natural tone. "
        "Do not change the meaning, do not answer the question, and do not add information. "
        "Provide only the rewritten sentence, nothing else."
    )
    response = llama_client.chat.completions.create(
        model="meta-llama/Llama-3.3-70B-Instruct-Turbo-Free",
        messages=[{"role": "system", "content": prompt},
                  {"role": "user", "content": text}],
    )
    return response.choices[0].message.content

In [ ]:
reformulated_texts = []

for text, intent in zip(texts, true_labels):
    reformulated_text = rewrite_with_intent(text) 
    reformulated_texts.append(reformulated_text)

# Associer les reformulations avec les labels
reformulated_data = [{"original": orig, "reformulated": reform, "intent": intent} 
                     for orig, reform, intent in zip(texts, reformulated_texts, true_labels)]


In [97]:
reformulated_data = [{"original": orig, "reformulated": reform, "intent": intent} 
                     for orig, reform, intent in zip(texts, reformulated_texts, true_labels)]

In [ ]:
with open("C:/ProjetMaster/text_clustering/scripts/reformulated_data.json", "w", encoding="utf-8") as f:
    json.dump(reformulated_data, f, ensure_ascii=False, indent=4)

In [ ]:
with open("C:/ProjetMaster/text_clustering/scripts/reformulated_data.json", "r", encoding="utf-8") as f:
    data = json.load(f)

print(f"✅ {len(data)} entrées chargées !")
print("Exemple :", data[:3])


✅ 4675 entrées chargées !
Exemple : [{'original': 'in spanish, meet me tomorrow is said how', 'reformulated': 'In Spanish, the phrase to ask someone to meet you tomorrow is expressed as follows: ¿Qué se dice "meet me tomorrow" en español! or more naturally, "¿Cómo se dice \'meet me tomorrow\' en español?"', 'intent': 'translate'}, {'original': 'in french, how do i say, see you later', 'reformulated': 'In French, how do you express "see you later"?', 'intent': 'translate'}, {'original': 'how do you say hello in japanese', 'reformulated': 'What is the Japanese word for hello.', 'intent': 'translate'}]


In [5]:
intents = []

# Parcourir les données et extraire les informations
for entry in data:
    print(entry)
    print("-"*100)
    if isinstance(entry, dict):
        intent = entry.get('intent', '')
        intents.append(intent)

{'original': 'in spanish, meet me tomorrow is said how', 'reformulated': 'In Spanish, the phrase to ask someone to meet you tomorrow is expressed as follows: ¿Qué se dice "meet me tomorrow" en español! or more naturally, "¿Cómo se dice \'meet me tomorrow\' en español?"', 'intent': 'translate'}
----------------------------------------------------------------------------------------------------
{'original': 'in french, how do i say, see you later', 'reformulated': 'In French, how do you express "see you later"?', 'intent': 'translate'}
----------------------------------------------------------------------------------------------------
{'original': 'how do you say hello in japanese', 'reformulated': 'What is the Japanese word for hello.', 'intent': 'translate'}
----------------------------------------------------------------------------------------------------
{'original': 'how do i ask about the weather in chinese', 'reformulated': "What's the best way to inquire about the weather when s

In [6]:
# Compter le nombre d'intentions uniques
unique_intents = set(intents)
print(f"Nombre d'intentions uniques: {len(unique_intents)}")

Nombre d'intentions uniques: 150


In [7]:
from collections import Counter

# Comptage des occurrences de chaque intent
intent_counts = Counter(intents)

# Affichage des résultats
print("Nombre d'exemples par intent :")
for intent, count in intent_counts.items():
    print(f"{intent}: {count}")


Nombre d'exemples par intent :
translate: 120
transfer: 120
timer: 120
definition: 120
meaning_of_life: 120
insurance_change: 120
find_phone: 120
travel_alert: 120
pto_request: 120
improve_credit_score: 120
fun_fact: 120
change_language: 120
payday: 120
replacement_card_duration: 120
time: 120
application_status: 120
flight_status: 95
flip_coin: 20
change_user_name: 20
where_are_you_from: 20
shopping_list_update: 20
what_can_i_ask_you: 20
maybe: 20
oil_change_how: 20
restaurant_reservation: 20
balance: 20
confirm_reservation: 20
freeze_account: 20
rollover_401k: 20
who_made_you: 20
distance: 20
user_name: 20
timezone: 20
next_song: 20
transactions: 20
restaurant_suggestion: 20
rewards_balance: 20
pay_bill: 20
spending_history: 20
pto_request_status: 20
credit_score: 20
new_card: 20
lost_luggage: 20
repeat: 20
mpg: 20
oil_change_when: 20
yes: 20
travel_suggestion: 20
insurance: 20
todo_list_update: 20
reminder: 20
change_speed: 20
tire_pressure: 20
no: 20
apr: 20
nutrition_info: 20
cale

In [8]:
import random
from collections import defaultdict

# Regrouper les phrases par intent
intent_dict = defaultdict(list)
for entry in data:
    intent_dict[entry["intent"]].append((entry["original"], entry["reformulated"]))

# Sélectionner 20 phrases par intent
selected_originals = []
selected_reformulated = []
true_labels = []

for intent, pairs in intent_dict.items():
    sampled_pairs = random.sample(pairs, min(20, len(pairs)))  # Prendre max 20 exemples ou tout si < 20
    selected_originals.extend([p[0] for p in sampled_pairs])  # Ajouter les "original"
    selected_reformulated.extend([p[1] for p in sampled_pairs])  # Ajouter les "reformulated"
    true_labels.extend([intent] * len(sampled_pairs))  # Ajouter le label intent correspondant

### Vectorization with all-MiniLM-L6-v2

In [ ]:
embeddings = minilm_emb_model.encode(reformulated_texts, convert_to_tensor=True)
original_embeddings = minilm_emb_model.encode(selected_originals, convert_to_tensor=True)
reformulated_embeddings = minilm_emb_model.encode(selected_reformulated, convert_to_tensor=True)

In [143]:
# Afficher la taille des embeddings
print(f"Originals embeddings shape: {original_embeddings[0].shape}")
print(f"Reformulated embeddings shape: {reformulated_embeddings.shape}")

Originals embeddings shape: torch.Size([384])
Reformulated embeddings shape: torch.Size([3000, 384])


### Vectorization with Instructor 

In [ ]:
reformulated_embeddings = inst_emb_model.encode(
    selected_reformulated,
    batch_size=16,
    convert_to_numpy=True,
    show_progress_bar=True
)

Batches: 100%|██████████| 188/188 [13:25<00:00,  4.29s/it]


In [ ]:
original_embeddings = inst_emb_model.encode(
    selected_originals,
    batch_size=16,
    convert_to_numpy=True,
    show_progress_bar=True
)

Batches: 100%|██████████| 188/188 [12:24<00:00,  3.96s/it]


In [161]:
# Afficher la taille des embeddings
print(f"Originals embeddings shape: {original_embeddings[0].shape}")

Originals embeddings shape: (768,)


### Keyphrases Extraction

#### With Few Shot prompting

In [12]:
def extract_keywords(sentence):
    prompt = """ 
    You are an expert in extracting the most relevant keywords from asentence to capture its intent for clustering.
    INSTRUCTIONS : 
    Focus on words that best represent the core meaning and purpose of the sentence. 
    Do not answer the question in the sentence. 
    Provide only the extracted keywords, separated by commas, without any explanation or additional text.

    EXAMPLES : 
    Example 1 :
    Sentence : I'm looking for my phone and I could use some assistance in finding it.
    Key words : looking for phone, finding phone, assistance in finding phone

    Example 2 : 
    Sentence : I'm looking to apply for a new credit card that fits my specific requirements.
    Key words : new credit card, card which fits requirements

    Example 3 : 
    Sentence : "What are the ways to say goodbye in French?",
    Key words : translation, translate goodbye to french word.

    Do the same with : 
    """

    prompt += f"Sentence {sentence}"

    chat_response = mistral_client.chat.complete(
        model= mistral,
        messages = [
            {
                "role": "system", "content": prompt,
            },
        ]
    )
    return chat_response.choices[0].message.content

#### With Zero Shot prompting

In [ ]:
def extract_keywords(sentence):
    prompt = """ 
    You are an expert in extracting the most relevant keywords from asentence to capture its intent for clustering.
    INSTRUCTIONS : 
    Focus on words that best represent the core meaning and purpose of the sentence. 
    Do not answer the question in the sentence. 
    Provide only the extracted keywords, separated by commas, without any explanation or additional text.

    Do the same with : 
    """

    prompt += f"Sentence {sentence}"

    chat_response = mistral_client.chat.complete(
        model= mistral,
        messages = [
            {
                "role": "system", "content": prompt,
            },
        ]
    )
    return chat_response.choices[0].message.content

In [ ]:
import json
from collections import defaultdict

with open("C:/projetsAlternance/projetMasterGit/Clustering_and_LLMs/text_clustering/scripts/reforumulated_data_with_domain.json", "r", encoding="utf-8") as f:
    data = json.load(f)

# Regrouper toutes les reformulations par intent
grouped_by_intent = defaultdict(list)
for item in data:
    grouped_by_intent[item["intent"]].append(item["reformulated"])

# Récupérer les 20 premières par intent
selected_examples = []
for intent, reformulations in grouped_by_intent.items():
    for reform in reformulations[:20]:
        selected_examples.append({
            "reformulated": reform,
            "intent": intent
        })


In [48]:
with open("C:/projetsAlternance/projetMasterGit/Clustering_and_LLMs/text_clustering/scripts/key_phrases_data.json", "r", encoding="utf-8") as f:
    data = json.load(f)

In [52]:
sentences_to_emb = []
intents = []
for item in data:
    stc = item["sentence"]
    intent = item["intent"]
    keyw = item["key_phrase"]
    

    full_text = f"{stc}... Keywords : {keyw}"
    sentences_to_emb.append(full_text)
    intents.append(intent)

In [56]:
print(len(sentences_to_emb))

3000


In [ ]:
from collections import defaultdict

sentences_to_emb = []
intents = []

# Pour compter les occurrences de chaque intent
intent_counts = defaultdict(int)

# Limite par intent
limit_per_intent = 20


for item in data:
    stc = item["sentence"]
    intent = item["intent"]
    keyw = item["key_phrase"]

    if isinstance(keyw, list):
        keyw = " ".join(keyw)

    if intent_counts[intent] < limit_per_intent:
        full_text = f"{stc}... Keywords : {keyw}"
        sentences_to_emb.append(full_text)
        intents.append(intent)
        intent_counts[intent] += 1


In [66]:
print(len(set(intents)))

150


In [60]:
embeddings = minilm_emb_model.encode(sentences_to_emb)

In [68]:
kmeans = KMeans(n_clusters=150, random_state=42)
labels = kmeans.fit_predict(embeddings)

In [ ]:
nmi = compute_nmi(intents, labels)
print(f"NMI = {nmi:.4F}")
acc = compute_hungarian_accuracy(intents, labels)
print(f"ACC = {acc:.4F}")
ari = compute_ari(intents, labels)
print(f"ARI = {ari:.4F}")

## Hierarchical Clustering 

In [ ]:
intent_to_domain = {
    # Banking
    "transfer": "Banking", "transactions": "Banking", "balance": "Banking", "freeze_account": "Banking", 
    "pay_bill": "Banking", "bill_balance": "Banking", "bill_due": "Banking", "interest_rate": "Banking",
    "routing": "Banking", "min_payment": "Banking", "order_checks": "Banking", 
    "pin_change": "Banking", "report_fraud": "Banking", "account_blocked": "Banking", 
    "spending_history": "Banking",

    # Credit cards
    "credit_score": "Credit cards", "report_lost_card": "Credit cards", "credit_limit": "Credit cards", 
    "rewards_balance": "Credit cards", "new_card": "Credit cards", "application_status": "Credit cards", 
    "card_declined": "Credit cards", "international_fees": "Credit cards", "apr": "Credit cards", 
    "redeem_rewards": "Credit cards", "credit_limit_change": "Credit cards", "damaged_card": "Credit cards", 
    "replacement_card_duration": "Credit cards", "improve_credit_score": "Credit cards", 
    "expiration_date": "Credit cards",

    # Kitchen & Dining
    "recipe": "Kitchen & Dining", "restaurant_reviews": "Kitchen & Dining", "calories": "Kitchen & Dining",
    "nutrition_info": "Kitchen & Dining", "restaurant_suggestion": "Kitchen & Dining", 
    "ingredients_list": "Kitchen & Dining", "ingredient_substitution": "Kitchen & Dining", 
    "cook_time": "Kitchen & Dining", "food_last": "Kitchen & Dining", "meal_suggestion": "Kitchen & Dining", 
    "restaurant_reservation": "Kitchen & Dining", "confirm_reservation": "Kitchen & Dining", 
    "how_busy": "Kitchen & Dining", "cancel_reservation": "Kitchen & Dining", 
    "accept_reservations": "Kitchen & Dining",

    # Home
    "shopping_list": "Home", "shopping_list_update": "Home", "next_song": "Home", "play_music": "Home", 
    "update_playlist": "Home", "todo_list": "Home", "todo_list_update": "Home", "calendar": "Home", 
    "calendar_update": "Home", "what_song": "Home", "order": "Home", "order_status": "Home", 
    "reminder": "Home", "reminder_update": "Home", "smart_home": "Home",

    # Auto & commute
    "traffic": "Auto & commute", "directions": "Auto & commute", "gas": "Auto & commute", 
    "gas_type": "Auto & commute", "distance": "Auto & commute", "current_location": "Auto & commute", 
    "mpg": "Auto & commute", "oil_change_when": "Auto & commute", "oil_change_how": "Auto & commute", 
    "jump_start": "Auto & commute", "uber": "Auto & commute", "schedule_maintenance": "Auto & commute", 
    "last_maintenance": "Auto & commute", "tire_pressure": "Auto & commute", "tire_change": "Auto & commute",

    # Travel
    "book_flight": "Travel", "book_hotel": "Travel", "car_rental": "Travel", "travel_suggestion": "Travel",
    "travel_alert": "Travel", "travel_notification": "Travel", "carry_on": "Travel", "timezone": "Travel", 
    "vaccines": "Travel", "translate": "Travel", "flight_status": "Travel", "international_visa": "Travel",
    "lost_luggage": "Travel", "plug_type": "Travel", "exchange_rate": "Travel",

    # Utility
    "time": "Utility", "alarm": "Utility", "share_location": "Utility", "find_phone": "Utility", 
    "weather": "Utility", "text": "Utility", "spelling": "Utility", "make_call": "Utility", "timer": "Utility", 
    "date": "Utility", "calculator": "Utility", "measurement_conversion": "Utility", "flip_coin": "Utility", 
    "roll_dice": "Utility", "definition": "Utility",

    # Work
    "direct_deposit": "Work", "pto_request": "Work", "taxes": "Work", "payday": "Work", "w2": "Work", 
    "pto_balance": "Work", "pto_request_status": "Work", "next_holiday": "Work", "insurance": "Work", 
    "insurance_change": "Work", "schedule_meeting": "Work", "pto_used": "Work", 
    "meeting_schedule": "Work", "rollover_401k": "Work", "income": "Work",

    # Small talk
    "greeting": "Small talk", "goodbye": "Small talk", "tell_joke": "Small talk", 
    "where_are_you_from": "Small talk", "how_old_are_you": "Small talk", "what_is_your_name": "Small talk", 
    "who_made_you": "Small talk", "thank_you": "Small talk", "what_can_i_ask_you": "Small talk", 
    "what_are_your_hobbies": "Small talk", "do_you_have_pets": "Small talk", "are_you_a_bot": "Small talk", 
    "meaning_of_life": "Small talk", "who_do_you_work_for": "Small talk", "fun_fact": "Small talk",

    # Meta 
    "change_ai_name": "Meta", "change_user_name": "Meta", "cancel": "Meta", "user_name": "Meta", 
    "reset_settings": "Meta", "whisper_mode": "Meta", "repeat": "Meta", "no": "Meta",
    "yes": "Meta", "maybe": "Meta", "change_language": "Meta", "change_accent": "Meta",
    "change_volume": "Meta", "change_speed": "Meta", "sync_device": "Meta",
}

In [ ]:
def mmr(doc_embeddings, centroid, k=5, lambda_param=0.5):
    doc_embeddings = np.array(doc_embeddings)
    centroid = np.array(centroid).reshape(1, -1)

    similarities = cosine_similarity(doc_embeddings, centroid).flatten()
    selected = []
    candidates = list(range(len(doc_embeddings)))

    k = min(k, len(doc_embeddings)) 
    
    for _ in range(k):
        if not selected:
            selected_idx = np.argmax(similarities)
        else:
            selected_similarities = cosine_similarity(doc_embeddings[candidates], doc_embeddings[selected])
            max_sim = np.max(selected_similarities, axis=1)
            mmr_score = lambda_param * similarities[candidates] - (1 - lambda_param) * max_sim
            selected_idx = candidates[np.argmax(mmr_score)]
        selected.append(selected_idx)
        candidates.remove(selected_idx)
    return selected

In [ ]:
def generate_cluster_description(phrases):
    prompt = """
    Here is a set of phrases that are grouped into a cluster. Can you provide a detailed description of what this cluster represents, including the main topics and intent behind the phrases, using affirmative sentences and avoiding repeating the input phrases? 
    Here are 2 examples of what you'll get as input and what you should do:

    Example 1:
    Cluster Phrases:
    1. I want to check the balance of my bank account.
    2. How can I view my bank details?
    3. I need to know the balance of my account.
    Cluster Description: This cluster contains questions related to checking bank balances. The intent behind these phrases is to ask for information about the account's balance or financial details.

    Example 2:
    Cluster Phrases:
    1. Where is my tracking number?
    2. How can I track my package?
    3. I want to know the status of my delivery.
    Cluster Description: This cluster contains requests related to tracking packages. The intent is to inquire about the current position of a shipment or parcel.

    Now, here are the phrases for your cluster:
    """
    
    for i, phrase in enumerate(phrases, 1):
        prompt += f"{i}. {phrase}\n"

    # Add the expected output format
    prompt += """
    Cluster Description:
    """

    # Tokenizer le prompt et le passer au modèle
    chat_response = mistral_client.chat.complete(
        model= mistral,
        messages = [
            {
                "role": "system", "content": prompt,
            },
        ]
    )
    return chat_response.choices[0].message.content

In [ ]:
with open("C:/ProjetMaster/text_clustering/scripts/reformulated_data.json", "r", encoding="utf-8") as f:
    data = json.load(f)

# Ajout du champ domain à chaque entrée
for item in data:
    intent = item["intent"]
    domain = intent_to_domain.get(intent, "Unknown")
    item["domain"] = domain

# Sauvegarde dans un fichier JSON
with open("reforumulated_data_with_domain.json", "w", encoding="utf-8") as f:
    json.dump(data, f, indent=4, ensure_ascii=False)

print("✅ JSON avec les domaines enregistré sous 'data_with_domain.json'")

✅ JSON avec les domaines enregistré sous 'data_with_domain.json'


In [7]:
with open("reforumulated_data_with_domain.json", "r", encoding="utf-8") as f:
    data = json.load(f)

df = pd.DataFrame(data, columns=["original", "reformulated", "intent", "domain"])

print(df.head())

                                    original  \
0   in spanish, meet me tomorrow is said how   
1     in french, how do i say, see you later   
2           how do you say hello in japanese   
3  how do i ask about the weather in chinese   
4  how can i say "cancel my order" in french   

                                        reformulated     intent  domain  
0  In Spanish, the phrase to ask someone to meet ...  translate  Travel  
1     In French, how do you express "see you later"?  translate  Travel  
2               What is the Japanese word for hello.  translate  Travel  
3  What's the best way to inquire about the weath...  translate  Travel  
4     How can I express "cancel my order" in French!  translate  Travel  


In [24]:
reformulated_sentences = df["reformulated"].tolist()

In [25]:
reformulated_sentences_preprocess = [preprocess_text(sentence) for sentence in reformulated_sentences]

In [58]:
embeddings = minilm_emb_model.encode(reformulated_sentences_preprocess)

In [30]:
embeddings = inst_emb_model.encode(
    reformulated_sentences_preprocess,
    batch_size=16,
    convert_to_numpy=True,
    show_progress_bar=True
)

Batches: 100%|██████████| 293/293 [13:01<00:00,  2.67s/it]


In [59]:
df["embeddings"] = list(embeddings)

### Clustering L2

In [60]:
num_clusters_l2 = 150

clustering_l2 = KMeans(n_clusters=num_clusters_l2, random_state=42)
labels_l2 = clustering_l2.fit_predict(embeddings)

# Ajouter les labels L2 au DataFrame
df["cluster_L2"] = labels_l2

In [ ]:
from sklearn.metrics import silhouette_score
score_silhouette = silhouette_score(embeddings, labels_l2, metric='cosine')
print(f"Silhouette Score (cosine): {score_silhouette:.4f}")
nmi = compute_nmi(df["intent"], labels_l2)
print(f"NMI = {nmi:.4F}")
acc = compute_hungarian_accuracy(df["intent"], labels_l2)
print(f"ACC = {acc:.4F}")
ari = compute_ari(df["intent"], labels_l2)
print(f"ARI = {ari:.4F}")

In [ ]:
from collections import defaultdict

# Nombre de documents à extraire par cluster
k = 5

# Grouper les phrases par cluster L2
cluster_groups = defaultdict(list)
embedding_groups = defaultdict(list)
index_groups = defaultdict(list)
centroid_groups = defaultdict(list)

for i, row in df.iterrows():
    print(f"i = {i}")
    c = row["cluster_L2"]
    print(f"c = {c}")
    cluster_groups[c].append(row["reformulated"])
    embedding_groups[c].append(row["embeddings"])
    index_groups[c].append(i)
    print("-"*300)

# Extraire les documents représentatifs par cluster
representative_docs = {}

for cluster_id in cluster_groups:
    embeddings = embedding_groups[cluster_id]
    centroid = np.mean(embeddings, axis=0)
    centroid_groups[cluster_id].append(centroid)
    if len(embeddings) == 0:
        continue  # cluster vide
    
    elif len(embeddings) <= k:
        selected_rows = index_groups[cluster_id]  # on garde tous les points
    else:
        selected_indices = mmr(embeddings, centroid, k=k)
        selected_rows = [index_groups[cluster_id][i] for i in selected_indices]
    
    representative_docs[cluster_id] = df.loc[selected_rows]

In [ ]:
import time

remaining_cluster_details = {}

# Appliquer seulement aux clusters qui ne sont pas encore traités
for cluster_id, docs in representative_docs.items():
    phrases = docs["reformulated"].tolist()

    try:
        description = generate_cluster_description(phrases)
        description_text = description[0] if isinstance(description, list) else description

        remaining_cluster_details[cluster_id] = {"description": description_text}

        print(f"[Cluster {cluster_id}] Description : {description_text}")
        print("-" * 200)

        # Pause entre les requêtes pour éviter le rate limit
        time.sleep(4)

    except Exception as e:
        print(f"Erreur pour le cluster {cluster_id} : {e}")

[Cluster 7] Description : This cluster represents queries and commands related to language preferences and translations. The main topics include setting or changing the language to Spanish, requesting translations in Spanish, and expressing phrases in other languages like Italian. The intent behind these phrases is to seek assistance with language settings or to obtain specific translations. Additionally, the cluster shows an interest in multilingual communication, with a particular focus on Spanish.
--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------
[Cluster 14] Description : This cluster represents a mix of inquiries and requests related to ordering and purchasing products, as well as checking the status of deliveries. The intent behind these phrases includes wanting to know if an ordered item has been delivered successfully, expressing

In [ ]:
description_embeddings = {}

for cluster_id, cluster_info in remaining_cluster_details.items():
    description = cluster_info["description"]
    description_emb = minilm_emb_model.encode(description)
    description_embeddings[cluster_id] = description_emb

In [71]:
# Créer un dictionnaire pour stocker les informations du cluster
cluster_info = []

w1 = 1  # Poids pour le centroid
w2 = 1 
for cluster_id in index_groups:
    description_embedding = description_embeddings.get(cluster_id, None)
    centroid = np.array(centroid_groups.get(cluster_id, None))

    if description_embedding is not None and centroid is not None:
        weighted_centroid = w1 * centroid
        weighted_description = w2 * description_embedding
        print(weighted_description.shape)
        print(weighted_centroid.shape)
        combined_embedding = np.concatenate([weighted_centroid.flatten(), weighted_description])
        #combined_embedding = np.concatenate([centroid.flatten(), description_embedding])
        print(f"Taille de l'embedding combiné pour le cluster {cluster_id}: {combined_embedding.shape}")
        cluster_data = df[df["cluster_L2"] == cluster_id].iloc[0] 
        print(f"cluster_data = {cluster_data}")
        intent = cluster_data["intent"]
        print(f"intent = {intent}")
        domain = cluster_data["domain"]
        print(f"domain = {domain}")
        print("-"*100)

        # Ajouter l'information dans la liste
        cluster_info.append({
            "cluster_id": cluster_id,
            "combined_embedding": combined_embedding,
            "intent": intent,
            "domain": domain
        })
    else:
        print(f"Cluster {cluster_id} n'a pas d'embedding ou de centroid.")

# Créer un DataFrame avec les informations collectées
df_cluster_info = pd.DataFrame(cluster_info)

# Vérification du résultat
print(df_cluster_info.head())

(384,)
(1, 384)
Taille de l'embedding combiné pour le cluster 7: (768,)
cluster_data = original                 in spanish, meet me tomorrow is said how
reformulated    In Spanish, the phrase to ask someone to meet ...
intent                                                  translate
domain                                                     Travel
cluster_L2                                                      7
embeddings      [-0.018516315, 0.0069776387, 0.07012044, 0.052...
Name: 0, dtype: object
intent = translate
domain = Travel
----------------------------------------------------------------------------------------------------
(384,)
(1, 384)
Taille de l'embedding combiné pour le cluster 14: (768,)
cluster_data = original                   in french, how do i say, see you later
reformulated       In French, how do you express "see you later"?
intent                                                  translate
domain                                                     Travel
cluste

### Clustering L1

In [72]:
X = np.array(df_cluster_info["combined_embedding"].tolist())
X = X.reshape(X.shape[0], -1)
print(X.shape)

true_labels_l1 = df_cluster_info["domain"].values
# Appliquer KMeans pour faire un clustering L1
num_clusters_l1 = 10   
clustering_l1 = KMeans(n_clusters=num_clusters_l1, random_state=42)
labels_l1 = clustering_l1.fit_predict(X)

(150, 768)


In [ ]:
# Comparer NMI
nmi = normalized_mutual_info_score(true_labels_l1, labels_l1)
ari = adjusted_rand_score(true_labels_l1, labels_l1)
acc = compute_hungarian_accuracy(true_labels_l1, labels_l1)
print(f"NMI = {nmi:.4f}")
print(f"Acc = {acc:.4f}")
print(f"ARI = {ari:.4f}")

# During Clustering

## K-LLMmeans

In [ ]:
def get_embeddings(texts, model_name):
    embeddings = model_name.encode(
        texts,
        batch_size=16,
        convert_to_numpy=True,
        show_progress_bar=True
    )
    
    return embeddings

In [ ]:
def generate_summary_with_llm(documents):

    prompt = """You are an expert in summarizing clusters of documents based on their underlying themes and content. Below are examples of how to effectively summarize such clusters:
    Example 1:
    Document 1: "Artificial intelligence (AI) is a branch of computer science that focuses on creating intelligent machines capable of performing tasks that typically require human intelligence.
    Document 2: "Machine learning is a subset of AI that enables systems to learn from data and improve over time without being explicitly programmed.
    Document 3: "Deep learning is a further subset of machine learning, where neural networks are used to model complex patterns in large datasets.
    Summary: This cluster of documents discusses artificial intelligence (AI), with a focus on machine learning and deep learning technologies. The main theme is the development of AI systems and their ability to improve through data-driven learning processes.

    Example 2:
    Document 1: "Recommendation systems are widely used in e-commerce platforms to suggest products based on users' preferences and past behaviors.
    Document 2: "Collaborative filtering is a popular method in recommendation systems, which predicts a user's preferences based on the preferences of similar users.
    Document 3: "Content-based filtering is another technique, which suggests products based on the similarity between a user's previous interactions and the attributes of other products.
    Summary: This cluster of documents is focused on recommendation systems, detailing techniques like collaborative filtering and content-based filtering, which are used to personalize product suggestions for users based on their behavior and preferences.

    Now, based on the following documents, please generate a concise and informative summary of the cluster that captures its central theme and the key concepts discussed:"""
    
    prompt += "\n".join(documents)

    # Tokenizer le prompt et le passer au modèle
    chat_response = mistral_client.chat.complete(
        model= mistral,
        messages = [
            {
                "role": "system", "content": prompt,
            },
        ],
        temperature=0.5
    )
    return chat_response.choices[0].message.content

In [ ]:
def assign_clusters(embeddings, centroids):
    labels = []
    # Calcul de la similarité cosinus entre chaque embedding et les centroids
    for emb in embeddings:
        similarities = cosine_similarity([emb], centroids)  # cosine_similarity attend des entrées sous forme de matrices
        labels.append(np.argmax(similarities))  # On sélectionne le centroïde avec la plus grande similarité
    return labels


In [118]:
# K-Means avec mise à jour des centroids via LLM
def k_llmmeans(documents, n_clusters, update_iter, total_iter, emb_model_name):
    embeddings = get_embeddings(documents, emb_model_name)
    
    kmeans = KMeans(n_clusters=n_clusters, init='k-means++')
    kmeans.fit(embeddings)
    centroids = kmeans.cluster_centers_
    labels = kmeans.labels_

    for iter in range(total_iter):
        print(f"iter = {iter}")
        if iter % update_iter == 0:
            print(">> Updating centroids via LLM summarization")
            # Mettre à jour les centroïdes avec LLM
            for j in range(n_clusters):
                # Extraire les indices des documents dans le cluster j
                cluster_indices = [i for i in range(len(documents)) if kmeans.labels_[i] == j]
                if not cluster_indices:
                    continue  

                cluster_embeds = [embeddings[i] for i in cluster_indices]
                cluster_texts = [documents[i] for i in cluster_indices]
                print(f"cluster_texts : {cluster_texts}")
                top_k = min(5, len(cluster_texts))  # adapte si moins de 5 docs
                selected_idxs = mmr(cluster_embeds, centroids[j], k=top_k, lambda_param=0.5)
                print(f"selected_idxs : {selected_idxs}")
                cluster_docs = [cluster_texts[i] for i in selected_idxs]
                time.sleep(3)
                # Générer un résumé avec le LLM
                summary = generate_summary_with_llm(cluster_docs)
                print(f"summary : {summary}")
                print("-"*200)
                # Re-calculer l'embedding du résumé (nouveau centroïde)
                summary_embedding = get_embeddings([summary], emb_model_name)[0]
                centroids[j] = summary_embedding
                
        else:
            print(">> Updating centroids via mean of cluster embeddings")
            # Mise à jour des centroïdes avec l'algorithme classique (moyenne des embeddings)
            for j in range(n_clusters):
                cluster_embeddings = [embeddings[i] for i in range(len(documents)) if kmeans.labels_[i] == j]
                if cluster_embeddings:
                    centroids[j] = np.mean(cluster_embeddings, axis=0)

        # Réassignation manuelle des documents aux clusters
        labels = assign_clusters(embeddings, centroids)
        
    return labels, centroids

In [ ]:
with open("reforumulated_data_with_domain.json", "r", encoding="utf-8") as f:
    data = json.load(f)

df = pd.DataFrame(data, columns=["original", "reformulated", "intent", "domain"])

In [111]:
df_sampled = df.groupby('intent').apply(lambda x: x.sample(n=20, random_state=42)).reset_index(drop=True)

C:\Users\melis\AppData\Local\Temp\ipykernel_69692\2721342477.py:1: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  df_sampled = df.groupby('intent').apply(lambda x: x.sample(n=20, random_state=42)).reset_index(drop=True)


In [112]:
print(df_sampled['intent'].value_counts())

intent
accept_reservations          20
reminder                     20
repeat                       20
replacement_card_duration    20
report_fraud                 20
                             ..
greeting                     20
how_busy                     20
how_old_are_you              20
improve_credit_score         20
yes                          20
Name: count, Length: 150, dtype: int64


In [119]:
# Paramètres du clustering
n_clusters = 150 
update_iter = 5
total_iter = 50
labels, centroids = k_llmmeans(df_sampled["reformulated"], n_clusters, update_iter, total_iter, inst_emb_model)

Batches: 100%|██████████| 188/188 [13:30<00:00,  4.31s/it]


iter = 0
>> Updating centroids via LLM summarization
cluster_texts : ['What time is my American Airlines flight scheduled to land', 'At what time is boarding for my flight scheduled to start?', 'What time is my flight scheduled to arrive?', 'At what time can I expect the arrival of my flight', 'What time is my flight scheduled to land?', 'At what time is my flight expected to arrive', 'I need to know the boarding time for my upcoming flight.', 'What is the scheduled arrival time of my flight?']
selected_idxs : [2, 6, 0, 1, 4]
summary : This cluster of documents revolves around air travel inquiries, specifically focusing on timing details related to flights. The key concepts discussed include the scheduled arrival time of flights, the boarding time for upcoming flights, and the landing time, particularly for American Airlines. The central theme is the need for precise timing information to plan and coordinate travel effectively.
----------------------------------------------------------

Batches: 100%|██████████| 1/1 [00:00<00:00,  1.01it/s]


cluster_texts : ['For how many years have you been living in this place.', 'What is the total number of days that I have used it for.']
selected_idxs : [0, 1]
summary : Summary: "This cluster of documents centers around questions related to duration and usage, specifically inquiring about the length of time an individual has lived in a particular location and the total number of days a certain item or service has been used."
--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------


Batches: 100%|██████████| 1/1 [00:00<00:00,  1.07it/s]


...

cluster_texts : ['Make sure the doors are secure.', 'Check to make sure all the doors are locked.', 'Make sure the doors are locked.', 'Lock all the doors.', 'Lock all the doors.', 'Can you please check to make sure the doors are locked?', 'Please verify that the doors are locked.']
selected_idxs : [2, 5, 4, 1, 6]
summary : This cluster of documents revolves around the central theme of ensuring that doors are securely locked. The key concepts discussed include instructions and requests to check, verify, and lock all doors, emphasizing the importance of confirming that they are properly secured.
--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------


Batches: 100%|██████████| 1/1 [00:01<00:00,  1.02s/it]


cluster_texts : ['Do not synchronize with my phone.', 'I want to synchronize it with my phone.', 'I no longer want you to connect to my phone.', 'I no longer want to sync with my phone.', 'Stop synchronizing data with my phone.', 'Stop syncing with my phone.', 'I want to disconnect sync from my phone.', 'I want to disconnect from my phone.']
selected_idxs : [3, 1, 7, 4, 0]
summary : This cluster of documents revolves around the theme of managing the synchronization between a device and a phone. The key concepts discussed include the desire to either synchronize data with the phone or disconnect and stop the synchronization process.
--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------


Batches: 100%|██████████| 1/1 [00:01<00:00,  1.01s/it]


iter = 46
>> Updating centroids via mean of cluster embeddings
iter = 47
>> Updating centroids via mean of cluster embeddings
iter = 48
>> Updating centroids via mean of cluster embeddings
iter = 49
>> Updating centroids via mean of cluster embeddings


In [ ]:
nmi = normalized_mutual_info_score(df_sampled["intent"], labels)
ari = adjusted_rand_score(df_sampled["intent"], labels)
acc = compute_hungarian_accuracy(df_sampled["intent"], labels)
print(f"NMI = {nmi:.4f}")
print(f"Acc = {acc:.4f}")
print(f"ARI = {ari:.4f}")

# After Clustering

### LLM Correct

In [ ]:
def get_outliers(vectors, model, threshold=0.5):
    centroids = model.cluster_centers_
    labels = model.labels_
    distances = np.linalg.norm(vectors - centroids[labels], axis=1)
    outlier_indices = np.where(distances > threshold)[0]

    outlier_clusters = {idx: labels[idx] for idx in outlier_indices}
    return outlier_clusters

def get_top_k_nearest_clusters(doc_vector, centroids, k=5):
    dists = np.linalg.norm(centroids - doc_vector, axis=1)
    return np.argsort(dists)[:k]

def get_top_n_representative_docs(cluster_id, vectors, labels, centroids, n=3):
    cluster_indices = np.where(labels == cluster_id)[0]
    cluster_vectors = vectors[cluster_indices]
    dists = np.linalg.norm(cluster_vectors - centroids[cluster_id], axis=1)
    top_n_indices = cluster_indices[np.argsort(dists)[:n]]
    return top_n_indices

def classify_with_llm(outlier_doc, candidate_clusters, representatives, documents, llm_decision_function):
    prompt = """You are an expert in intent clustering and reassigning outliers. 
        You will be given:
        - A document to reassign
        - 5 clusters, each represented 3 typical documents
        Your task is to analyze the content and intent of the document, compare it with the cluster examples, and determine which existing cluster it should belong to.
        Please provide only the selected cluster.\n\n"""

    for i, cluster_id in enumerate(candidate_clusters):
        prompt += f"\nCluster {cluster_id}:\n"
        for doc_id in representatives[cluster_id]:
            prompt += f"- {documents[doc_id]}\n"
    prompt += f"Document :\n{outlier_doc}...\n\n" 
    prompt += "Which cluster should this super-point be assigned to?"
    return llm_decision_function(prompt)

def reassign_outliers(documents, vectors, model, llm_decision_function, threshold=0.5):
    centroids = model.cluster_centers_
    labels = model.labels_
    outliers = get_outliers(vectors, model, threshold)
    for idx, cluster in outliers.items():
        print(f"Index : {idx}, Cluster actuel : {cluster}")
    new_assignments = {}
    for idx in outliers:
        print(f"idx: {idx}")
        doc_vector = vectors[idx]
        candidate_clusters = get_top_k_nearest_clusters(doc_vector, centroids)
        
        representatives = {
            cluster_id: get_top_n_representative_docs(cluster_id, vectors, labels, centroids)
            for cluster_id in candidate_clusters
        }
        print(f"representatives : {representatives}")
        time.sleep(5)
        response = classify_with_llm(
            documents[idx],
            candidate_clusters,
            representatives,
            documents,
            llm_decision_function
        )
        print(f"response = {response}")
        match = re.search(r'\d+', response)
        if match:
            new_label= int(match.group())
        else:
            # Gérer le cas où aucun chiffre n'est trouvé
            print(f"Aucun chiffre trouvé dans la réponse : {response}")
            new_label = labels[idx]
        print(f"new_label = {new_label}")
        new_assignments[idx] = new_label
    return new_assignments


def ask_llm(prompt):
    chat_response = mistral_client.chat.complete(
        model= mistral,
        messages = [
            {
                "role": "system", "content": prompt,
            },
        ],
        temperature=0.3
    )
    return chat_response.choices[0].message.content

In [279]:
sentences = df_sampled["reformulated"]
embeddings = get_embeddings(sentences, minilm_emb_model)

Batches: 100%|██████████| 188/188 [00:11<00:00, 16.80it/s]


In [285]:
kmeans = KMeans(n_clusters=150, random_state=42)
labels = kmeans.fit_predict(embeddings)
new_labels = reassign_outliers(sentences, embeddings, kmeans, ask_llm)

Index : 1, Cluster actuel : 30
Index : 6, Cluster actuel : 30
Index : 9, Cluster actuel : 30
Index : 15, Cluster actuel : 30
Index : 16, Cluster actuel : 30
Index : 18, Cluster actuel : 30
Index : 26, Cluster actuel : 48
Index : 33, Cluster actuel : 139
Index : 37, Cluster actuel : 48
Index : 70, Cluster actuel : 1
Index : 80, Cluster actuel : 51
Index : 81, Cluster actuel : 51
Index : 83, Cluster actuel : 51
Index : 89, Cluster actuel : 51
Index : 95, Cluster actuel : 51
Index : 98, Cluster actuel : 51
Index : 100, Cluster actuel : 140
Index : 102, Cluster actuel : 140
Index : 105, Cluster actuel : 140
Index : 107, Cluster actuel : 140
Index : 108, Cluster actuel : 140
Index : 111, Cluster actuel : 140
Index : 112, Cluster actuel : 90
Index : 113, Cluster actuel : 70
Index : 114, Cluster actuel : 140
Index : 117, Cluster actuel : 140
Index : 120, Cluster actuel : 123
Index : 123, Cluster actuel : 123
Index : 124, Cluster actuel : 123
Index : 125, Cluster actuel : 105
Index : 126, Clus

In [286]:
original_labels = labels.copy()

In [287]:
true_labels = df_sampled["intent"]

In [ ]:
nmi_before = compute_nmi(true_labels, labels)
ari_before = compute_ari(true_labels, labels)
acc_before = compute_hungarian_accuracy(true_labels, labels)

print(f"nmi before = {nmi_before:.4f}")
print(f"ari before = {ari_before:.4f}")
print(f"acc before = {acc_before:.4f}")

In [ ]:
for idx, new_label in new_labels.items():
    labels[idx] = new_label

nmi_after = compute_nmi(true_labels, labels)
ari_after = compute_ari(true_labels, labels)
acc_after = compute_hungarian_accuracy(true_labels, labels)

print(f"nmi before = {nmi_after:.4f}")
print(f"ari before = {ari_after:.4f}")
print(f"acc before = {acc_after:.4f}")

# Before Clustering 

### Centroids generated by LLM

In [320]:
with open("C:/ProjetMaster/scripts/reforumulated_data_with_domain.json", "r", encoding="utf_8") as f:
    data = json.load(f)

df = pd.DataFrame(data, columns=["original", "reformulated", "intent", "domain"])
df_sampled = df.groupby('intent').apply(lambda x: x.sample(n=20, random_state=42)).reset_index(drop=True)

C:\Users\melis\AppData\Local\Temp\ipykernel_69692\3680981546.py:5: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  df_sampled = df.groupby('intent').apply(lambda x: x.sample(n=20, random_state=42)).reset_index(drop=True)


In [ ]:
def generate_centroid(sentences):
    prompt = """You are an expert generating a representative sentence for a cluster of intent documents.
    You will be given:
    - 4 sentences which belong to one intent cluster.
    
    Your task is to analyze the sentences' intent and generate a sentence that will represent all 4 sentences given. Do not give any explanation, only the representative sentence.
    
    Here is 2 examples : 
    Example 1 : 
        - sentence 1 : "What is the balance of my bank account?"
        - sentence 2 : "How much money is left in my account?"
        - sentence 3 : "I want to know the balance of my account."
        - sentence 4 :  "Can you give me the balance of my account?"
    the representative sentence is : "What is the current balance of my bank account?"

    Example 2 : 
        - sentence 1 : "I lost my card, block it."
        - sentence 2 : "My card was stolen, I want to block it."
        - sentence 3 : "Please block my card immediately."
        - sentence 4 :  "My bank card is missing, please block it."
    the representative sentence is : "I want to block my bank card due to its loss."

    Do the same with : 
    """
    for sentence in sentences:
        prompt += f"sentence : {sentence}\n"
    chat_response = mistral_client.chat.complete(
        model= mistral,
        messages = [
            {
                "role": "system", "content": prompt,
            },
        ],
        temperature=0.7
    )
    return chat_response.choices[0].message.content

In [ ]:
def generate_all_centroids(df):
    centroids = {}
    for intent, group in df.groupby('intent'):
        sentences_for_centroid = group['reformulated'].sample(4, random_state=42).tolist()
        time.sleep(5)
        centroid = generate_centroid(sentences_for_centroid)
        if centroid:
            centroids[intent] = centroid
            print(f"centroid : {centroid}")
        else:
            print(f"Failed to generate centroid for intent: {intent}")
        print(f"-"*300)
    return centroids

In [350]:
centroids = generate_all_centroids(df_sampled)

centroid : "I need information or assistance with my vehicle maintenance or current travel status."
------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------
centroid : "I need assistance with my bank account or card, including fraud concerns, transaction history, account status, and routing numbers."
------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------
centroid : "I need information about my credit card or its services."
-----------------------------------------------------------------------------------

In [351]:
centroid_sentences = list(centroids.values())
print(centroid_sentences[0:5])

['"I need information or assistance with my vehicle maintenance or current travel status."', '"I need assistance with my bank account or card, including fraud concerns, transaction history, account status, and routing numbers."', '"I need information about my credit card or its services."', 'I need to add or check items on my to-do or shopping list.', '"What information do you need regarding food, recipes, or restaurant reservations?"']


In [ ]:
centroids_emb = minilm_emb_model.encode(centroid_sentences)
sentences_emb = minilm_emb_model.encode(df_sampled["reformulated"])
# 6. KMeans avec init LLM
kmeans = KMeans(n_clusters=150, init=centroids_emb)
labels = kmeans.fit_predict(sentences_emb)

In [ ]:
nmi = compute_nmi(df_sampled['domain'], labels)
ari = compute_ari(df_sampled['domain'], labels)
acc = compute_hungarian_accuracy(df_sampled['domain'], labels)

print(f"nmi before = {nmi:.4f}")
print(f"ari before = {ari:.4f}")
print(f"acc before = {acc:.4f}")

In [ ]:
prompt = "Represent the sentence for intent clustering: "

centroid_sentences_with_prompt = [prompt + sentence for sentence in centroid_sentences]
centroids_emb = inst_emb_model.encode(
    centroid_sentences_with_prompt,
    batch_size=16,
    convert_to_numpy=True,
    show_progress_bar=True
)

sentences_emb = np.load('reformulated_sentences_instruct_embeddings.npy')

In [ ]:
# 6. KMeans avec init LLM
kmeans = KMeans(n_clusters=150, init=centroids_emb)
labels = kmeans.fit_predict(sentences_emb)

In [ ]:
nmi = compute_nmi(df_sampled['domain'], labels)
ari = compute_ari(df_sampled['domain'], labels)
acc = compute_hungarian_accuracy(df_sampled['domain'], labels)

print(f"nmi before = {nmi:.4f}")
print(f"ari before = {ari:.4f}")
print(f"acc before = {acc:.4f}")